| Attack Technique   | Clean mAP@0.5 | Adversarial mAP@0.5 | Drop      |
|--------------------|---------------|---------------------|-----------|
| FGSM               | 0.927         | 0.312               | -0.615    |
| Fool Detectors     | 0.927         | 0.155               | -0.772    |
| UAP                | 0.927         | 0.443               | -0.484    |
| Disappearance DAG  | 0.935         | 0.547              | -0.388    |
| Targeted DAG       | 0.927         | 0.0947              | -0.8323   |
| PGD 0.02, 0.005    | 0.927         | 0.617               | -0.310   |
| PGD 0.1, 0.025      | 0.927        | 0.215               | -0.712   |

In [1]:
!curl -L "https://universe.roboflow.com/ds/glquRaJDf9?key=1kWinBXVTQ" > roboflow.zip; unzip roboflow.zip; rm roboflow.zip

Streaming output truncated to the last 5000 lines.
  inflating: train/labels/001677_JPG_jpg.rf.414e120831f7e7f30447cb3cb26bdc83.txt  
 extracting: train/labels/001677_JPG_jpg.rf.d0e22a225cbb317066ae2e6efd3dbcc2.txt  
  inflating: train/labels/001678_JPG_jpg.rf.21782caf845bde6574cb51b3f5c74490.txt  
  inflating: train/labels/001678_JPG_jpg.rf.4de99d4836e879bc0a6b13d15eefe346.txt  
  inflating: train/labels/001678_JPG_jpg.rf.d9b987c7dd66459a58b74d90a6970de7.txt  
  inflating: train/labels/001679_JPG_jpg.rf.7f8083798d74d6e40543f776ec116c6a.txt  
  inflating: train/labels/001679_JPG_jpg.rf.c11f3850b8f5630a0b21810e0a256c90.txt  
  inflating: train/labels/001679_JPG_jpg.rf.f0cdb80eb57c2cf67c5306cbf7c19aac.txt  
  inflating: train/labels/001680_JPG_jpg.rf.05690ffb9e45dcb471a95f0b96806331.txt  
  inflating: train/labels/001680_JPG_jpg.rf.8472e670be11dc0438f4a3e001e124bb.txt  
  inflating: train/labels/001680_JPG_jpg.rf.fc6132ab57b715e2192ea08bbc90067d.txt  
  inflating: train/labels/001681_JPG

In [2]:
!pip install ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 974.5/974.5 kB 27.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 116.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 90.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 54.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 14.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 96.7 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstal

In [3]:
import os
import torch
import numpy as np
from sklearn.cluster import KMeans
from torchvision import models, transforms
from PIL import Image
from util import sample_images_by_class , preprocess_image
from attacks import fgsm_attack_detector, pgd_attack_detector, targeted_dag_attack
import torch
from ultralytics import YOLO

import sys
import io
class SuppressPrints:  # Context manager to silence function output
    def __enter__(self):
        self._original_stdout = sys.stdout
        sys.stdout = io.StringIO()
    def __exit__(self, exc_type, exc_val, exc_tb):
        sys.stdout = self._original_stdout


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [4]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [5]:
model_path = "/content/drive/MyDrive/yolo/yolov8n_TrafficSigns.pt"
model = YOLO(model_path)

In [ ]:
import os
import random
from pathlib import Path

def get_image_label_paths(images_dir="/content/train/images", labels_dir="/content/train/labels"):
    """
    Selects image and label paths for adversarial attacks (Targeted DAG, PGD, FGSM, UAP).

    Returns:
        tuple: (dag_paths, pgd_paths, fgsm_paths, uap_paths), each an array of (image_path, label_path) tuples.
    """
    # 1. List all images and verify labels
    images_dir = Path(images_dir)
    labels_dir = Path(labels_dir)
    image_files = sorted([f for f in images_dir.glob("*.jpg") if f.is_file()])
    valid_pairs = []
    for img_path in image_files:
        label_path = labels_dir / f"{img_path.stem}.txt"
        if label_path.exists():
            valid_pairs.append((str(img_path), str(label_path)))

    print(f"Found {len(valid_pairs)} valid image-label pairs (expected ~10,590).")

    # 2. Identify images with Green Light (0) or Speed Limit 10 (1)
    weak_class_images = []
    for img_path, label_path in valid_pairs:
        try:
            with open(label_path, "r") as f:
                labels = f.readlines()
                if any(line.strip().startswith(("0 ", "1 ")) for line in labels):
                    weak_class_images.append((img_path, label_path))
        except Exception as e:
            print(f"Error reading {label_path}: {e}")

    print(f"Found {len(weak_class_images)} images with Green Light or Speed Limit 10.")

    # 3. Assign images to Targeted DAG (500: 250 weak + 250 random)
    dag_paths = []
    # Select 250 weak-class images (or all if <250)
    weak_sample = random.sample(weak_class_images, min(250, len(weak_class_images)))
    dag_paths.extend(weak_sample)
    # Select 250 random from remaining (exclude weak sample)
    remaining = [(i, l) for i, l in valid_pairs if (i, l) not in weak_sample]
    dag_paths.extend(random.sample(remaining, 250))

    # 4. Assign remaining images to PGD (2,000)
    remaining = [(i, l) for i, l in remaining if (i, l) not in dag_paths]
    pgd_paths = random.sample(remaining, 2000)

    # 5. Assign remaining to FGSM (1,500)
    remaining = [(i, l) for i, l in remaining if (i, l) not in pgd_paths]
    fgsm_paths = random.sample(remaining, 1500)

    # 6. Assign remaining to UAP (1,500)
    remaining = [(i, l) for i, l in remaining if (i, l) not in fgsm_paths]
    uap_paths = random.sample(remaining, 1500)

    # 7. Verify counts and uniqueness
    print(f"Targeted DAG: {len(dag_paths)} samples")
    print(f"PGD: {len(pgd_paths)} samples")
    print(f"FGSM: {len(fgsm_paths)} samples")
    print(f"UAP: {len(uap_paths)} samples")

    all_paths = dag_paths + pgd_paths + fgsm_paths + uap_paths
    assert len(set((i, l) for i, l in all_paths)) == 5500, "Duplicate paths detected!"

    return dag_paths, pgd_paths, fgsm_paths, uap_paths

# Run the selection
dag_paths, pgd_paths, fgsm_paths, uap_paths = get_image_label_paths()


Found 10590 valid image-label pairs (expected ~10,590).
Found 2224 images with Green Light or Speed Limit 10.
Targeted DAG: 500 samples
PGD: 2000 samples
FGSM: 1500 samples
UAP: 1500 samples


In [ ]:
import os
import torch
from torchvision.utils import save_image
from pathlib import Path
import shutil

# Output directories
output_image_dir = Path("PGD_augmented_images/images")
output_label_dir = Path("PGD_augmented_images/labels")
output_image_dir.mkdir(parents=True, exist_ok=True)
output_label_dir.mkdir(parents=True, exist_ok=True)

i = 0
# Attack loop
for img_path, label_path in pgd_paths:
    img_path = Path(img_path)
    label_path = Path(label_path)

    with SuppressPrints():
        adv_tensor = pgd_attack_detector(
            image_path=str(img_path),
            model_path=model_path,
            epsilon=0.1,  # Smaller for training robustness
            num_steps=10,
            step_size=0.025,
            conf_threshold=0.25,
            random_start=True,
            device="cuda" if torch.cuda.is_available() else "cpu"
            )

    # Skip if attack failed
    if adv_tensor is None:
        continue

    base_name = f"adv_pgd_{img_path.stem}"
    adv_image_path = output_image_dir / f"{base_name}.png"
    adv_label_path = output_label_dir / f"{base_name}.txt"

    save_image(adv_tensor.clone().detach().cpu(), adv_image_path, normalize=True)
    shutil.copy(label_path, adv_label_path)

    i += 1
    if i % 100 == 0:
        print(f"Generated {i} adversarial examples.")


Generated 100 adversarial examples.
Generated 200 adversarial examples.
Generated 300 adversarial examples.
Generated 400 adversarial examples.
Generated 500 adversarial examples.
Generated 600 adversarial examples.
Generated 700 adversarial examples.
Generated 800 adversarial examples.
Generated 900 adversarial examples.
Generated 1000 adversarial examples.
Generated 1100 adversarial examples.
Generated 1200 adversarial examples.
Generated 1300 adversarial examples.
Generated 1400 adversarial examples.
Generated 1500 adversarial examples.
Generated 1600 adversarial examples.
Generated 1700 adversarial examples.
Generated 1800 adversarial examples.
Generated 1900 adversarial examples.


In [ ]:
# prompt: zip PGD_augmented_images

!zip -r /content/PGD_augmented_images.zip /content/PGD_augmented_images


  adding: content/PGD_augmented_images/ (stored 0%)
  adding: content/PGD_augmented_images/labels/ (stored 0%)
  adding: content/PGD_augmented_images/labels/adv_pgd_00003_00027_00026_png.rf.240b0e4ec4b2a617a54b214a1ad6e622.txt (deflated 21%)
  adding: content/PGD_augmented_images/labels/adv_pgd_00008_00038_00019_png.rf.a453fa121b0c7df2bcf2a168ddd0fe66.txt (deflated 19%)
  adding: content/PGD_augmented_images/labels/adv_pgd_FisheyeCamera_1_00033_png.rf.6d65bd3913e93339bc15cbcdcec99ce3.txt (deflated 35%)
  adding: content/PGD_augmented_images/labels/adv_pgd_00002_00000_00026_png.rf.d46f9f6501359b9756c23e2262b3197e.txt (deflated 26%)
  adding: content/PGD_augmented_images/labels/adv_pgd_000847_jpg.rf.c628841b5736394b913c505851c45f05.txt (deflated 15%)
  adding: content/PGD_augmented_images/labels/adv_pgd_FisheyeCamera_1_00177_png.rf.4fd6ef4933c8ef258c42c8483dc6d9d7.txt (deflated 21%)
  adding: content/PGD_augmented_images/labels/adv_pgd_FisheyeCamera_1_00069_png.rf.899e0cd56a172c058802663

In [ ]:
!mv PGD_augmented_images.zip /content/drive/MyDrive/yolo

In [ ]:
!ls /content/drive/MyDrive/yolo

adversarial_data_set_dis_dag.zip	 adversarial_dataset_targeted_dag.zip
adversarial_data_set_fgsm.zip		 adversarial_data_set_UAP.zip
adversarial_data_set_fool_detectors.zip  fgsm_augmented_images.zip
adversarial_data_set_pgd_02.zip		 PGD_augmented_images.zip
adversarial_data_set_pgd_1.zip		 yolov8n_TrafficSigns.pt


In [ ]:
import os
import torch
from torchvision.utils import save_image
from pathlib import Path
import shutil

# Output directories
output_image_dir = Path("fgsm_augmented_images/images")
output_label_dir = Path("fgsm_augmented_images/labels")
output_image_dir.mkdir(parents=True, exist_ok=True)
output_label_dir.mkdir(parents=True, exist_ok=True)

i = 0
# Attack loop
for img_path, label_path in fgsm_paths:
    img_path = Path(img_path)
    label_path = Path(label_path)

    with SuppressPrints():
        adv_tensor = fgsm_attack_detector(
            image_path=str(img_path),
            model_path=model_path,
            epsilon=0.15,
            conf_threshold=0.25,
            device="cuda" if torch.cuda.is_available() else "cpu"
        )

    # Skip if attack failed
    if adv_tensor is None:
        continue

    base_name = f"adv_fgsm_{img_path.stem}"
    adv_image_path = output_image_dir / f"{base_name}.png"
    adv_label_path = output_label_dir / f"{base_name}.txt"

    save_image(adv_tensor.clone().detach().cpu(), adv_image_path, normalize=True)
    shutil.copy(label_path, adv_label_path)

    i += 1
    if i % 100 == 0:
        print(f"Generated {i} adversarial examples.")


Generated 100 adversarial examples.
Generated 200 adversarial examples.
Generated 300 adversarial examples.
Generated 400 adversarial examples.
Generated 500 adversarial examples.
Generated 600 adversarial examples.
Generated 700 adversarial examples.
Generated 800 adversarial examples.
Generated 900 adversarial examples.
Generated 1000 adversarial examples.
Generated 1100 adversarial examples.
Generated 1200 adversarial examples.
Generated 1300 adversarial examples.
Generated 1400 adversarial examples.


In [ ]:
!zip -r /content/fgsm_augmented_images.zip /content/fgsm_augmented_images

!mv fgsm_augmented_images.zip /content/drive/MyDrive/yolo


  adding: content/fgsm_augmented_images/ (stored 0%)
  adding: content/fgsm_augmented_images/labels/ (stored 0%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_000565_jpg.rf.908fd7d48a31ba1b8bab45838b8b98c1.txt (deflated 15%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_00002_00031_00027_png.rf.1487d6446c4d3d823ed1231bffd3f379.txt (deflated 24%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_000480_jpg.rf.029085b0c7e0b472a6d3accbdb595884.txt (deflated 31%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_road352_png.rf.9af0202482d2af127fed33305e693e71.txt (deflated 13%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_road482_png.rf.ab577b8450c69f9d8cda37908dd216b9.txt (deflated 13%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_00002_00015_00004_png.rf.bfac0c8d374b36dc75141baae164a658.txt (deflated 20%)
  adding: content/fgsm_augmented_images/labels/adv_fgsm_000949_jpg.rf.c8b693b2ade3d9a716babda9890f18a2.txt (deflated 37%)
  adding:

In [ ]:
delta_1_epsilon = torch.load("universal_delta_1_epsilon.pth")

In [ ]:
import os
import torch
from torchvision.utils import save_image
from pathlib import Path
import shutil

# Output directories
output_image_dir = Path("uap_augmented_images/images")
output_label_dir = Path("uap_augmented_images/labels")
output_image_dir.mkdir(parents=True, exist_ok=True)
output_label_dir.mkdir(parents=True, exist_ok=True)
delta_1_epsilon = delta_1_epsilon.to("cuda")

i = 0
# Attack loop
for img_path, label_path in uap_paths:
    img_path = Path(img_path)
    label_path = Path(label_path)

    test_image = preprocess_image(img_path).to("cuda")

    # Add the adversarial perturbation
    adv_tensor = test_image + delta_1_epsilon

    # Ensure the adversarial image is in a valid range (e.g., [0, 1])
    adv_tensor = torch.clamp(adv_tensor, 0, 1)

    # Skip if attack failed
    if adv_tensor is None:
        continue

    base_name = f"adv_uap_{img_path.stem}"
    adv_image_path = output_image_dir / f"{base_name}.png"
    adv_label_path = output_label_dir / f"{base_name}.txt"

    save_image(adv_tensor.clone().detach().cpu(), adv_image_path, normalize=True)
    shutil.copy(label_path, adv_label_path)

    i += 1
    if i % 100 == 0:
        print(f"Generated {i} adversarial examples.")


Generated 100 adversarial examples.
Generated 200 adversarial examples.
Generated 300 adversarial examples.
Generated 400 adversarial examples.
Generated 500 adversarial examples.
Generated 600 adversarial examples.
Generated 700 adversarial examples.
Generated 800 adversarial examples.
Generated 900 adversarial examples.
Generated 1000 adversarial examples.
Generated 1100 adversarial examples.
Generated 1200 adversarial examples.
Generated 1300 adversarial examples.
Generated 1400 adversarial examples.
Generated 1500 adversarial examples.


In [ ]:
!zip -r /content/uap_augmented_images.zip /content/uap_augmented_images
!mv uap_augmented_images.zip /content/drive/MyDrive/yolo
!ls /content/drive/MyDrive/yolo


  adding: content/uap_augmented_images/ (stored 0%)
  adding: content/uap_augmented_images/labels/ (stored 0%)
  adding: content/uap_augmented_images/labels/adv_uap_00000_00000_00011_png.rf.d90e4f357e6863b504552c29425e5a41.txt (deflated 18%)
  adding: content/uap_augmented_images/labels/adv_uap_00003_00000_00019_png.rf.9be039400ecf2ee302461849eb11c06e.txt (deflated 24%)
  adding: content/uap_augmented_images/labels/adv_uap_00001_00060_00000_png.rf.f147190985006ebe0a4886b529f9bd50.txt (deflated 23%)
  adding: content/uap_augmented_images/labels/adv_uap_000950_JPG_jpg.rf.ed045115e468d3a4f63990a2c7617745.txt (deflated 14%)
  adding: content/uap_augmented_images/labels/adv_uap_00000_00006_00029_png.rf.b4ad2ff118d9c1470180a74dbd7a662a.txt (deflated 19%)
  adding: content/uap_augmented_images/labels/adv_uap_road528_png.rf.318f9cf9f23f5e6b30faab08fd16fd0b.txt (deflated 28%)
  adding: content/uap_augmented_images/labels/adv_uap_FisheyeCamera_1_00362_png.rf.4f8f57c44b60eedbc040b81b67ab6238.txt 

In [ ]:
from operator import mod
import os
import torch
from torchvision.utils import save_image
from pathlib import Path
import shutil

# Output directories
output_image_dir = Path("Tdag_augmented_images/images")
output_label_dir = Path("Tdag_augmented_images/labels")
output_image_dir.mkdir(parents=True, exist_ok=True)
output_label_dir.mkdir(parents=True, exist_ok=True)

i = 0
for img_path, label_path in dag_paths:
    # Get original detections
    results = model(img_path)
    detected_classes = results[0].boxes.cls.int().tolist()

    # Determine target class
    adversarial_class = 1 if 0 in detected_classes else 0

    # Run attack with dynamic target
    with SuppressPrints():
        adv_tensor, success = targeted_dag_attack(
            image_path=img_path,
            model_path=model_path,
            num_iterations=20,
            gamma=0.003,
            adversarial_class=adversarial_class,
            conf_threshold=0.25,
            device="cuda" if torch.cuda.is_available() else "cpu"
        )

    # Skip if attack failed
    if adv_tensor is None:
        continue

    # Fixed line: Convert img_path to Path object to access stem
    base_name = f"adv_dag_{Path(img_path).stem}"
    adv_image_path = output_image_dir / f"{base_name}.png"
    adv_label_path = output_label_dir / f"{base_name}.txt"

    save_image(adv_tensor.clone().detach().cpu(), adv_image_path, normalize=True)
    shutil.copy(label_path, adv_label_path)

    i += 1
    if i % 100 == 0:
        print(f"Generated {i} adversarial examples.")


Streaming output truncated to the last 5000 lines.

0: 640x640 1 Speed Limit 80, 10.1ms
Speed: 0.0ms preprocess, 10.1ms inference, 1.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 Speed Limit 80, 11.7ms
Speed: 0.1ms preprocess, 11.7ms inference, 2.1ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 Speed Limit 80, 11.1ms
Speed: 0.0ms preprocess, 11.1ms inference, 1.9ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 Speed Limit 80, 10.1ms
Speed: 0.0ms preprocess, 10.1ms inference, 1.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 10.5ms
Speed: 0.0ms preprocess, 10.5ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 Speed Limit 80, 11.7ms
Speed: 0.0ms preprocess, 11.7ms inference, 1.8ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 Speed Limit 80, 13.5ms
Speed: 0.0ms preprocess, 13.5ms inference, 2.1ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 

In [ ]:
# prompt: zip Tdag_augmented_images

!zip -r /content/Tdag_augmented_images.zip /content/Tdag_augmented_images
!mv Tdag_augmented_images.zip /content/drive/MyDrive/yolo
!ls /content/drive/MyDrive/yolo


  adding: content/Tdag_augmented_images/ (stored 0%)
  adding: content/Tdag_augmented_images/labels/ (stored 0%)
  adding: content/Tdag_augmented_images/labels/adv_dag_000817_jpg.rf.68f00bacd64044c26863288fe30662fc.txt (deflated 55%)
  adding: content/Tdag_augmented_images/labels/adv_dag_000876_jpg.rf.f1484438b786c9bc2472eb5256de0105.txt (deflated 37%)
  adding: content/Tdag_augmented_images/labels/adv_dag_001628_JPG_jpg.rf.d9bd8fdce7633b12b74945d83f2ac9ae.txt (deflated 21%)
  adding: content/Tdag_augmented_images/labels/adv_dag_road464_png.rf.4271b0c2de0fab3e46a1b9a33186641e.txt (deflated 34%)
  adding: content/Tdag_augmented_images/labels/adv_dag_00001_00036_00016_png.rf.2e598c49c4d3a6bf8537f5b2fc81dacb.txt (deflated 16%)
  adding: content/Tdag_augmented_images/labels/adv_dag_000962_jpg.rf.b13038a44582de579d9ebd346baca2dd.txt (deflated 37%)
  adding: content/Tdag_augmented_images/labels/adv_dag_road474_png.rf.ad3e138e4e43508bccf7c4a88b3f0db6.txt (deflated 21%)
  adding: content/Tdag_

In [6]:
!ls /content/drive/MyDrive/yolo/uap_augmented_images.zip

adversarial_data_set_dis_dag.zip	 adversarial_data_set_UAP.zip
adversarial_data_set_fgsm.zip		 fgsm_augmented_images.zip
adversarial_data_set_fool_detectors.zip  PGD_augmented_images.zip
adversarial_data_set_pgd_02.zip		 Tdag_augmented_images.zip
adversarial_data_set_pgd_1.zip		 uap_augmented_images.zip
adversarial_dataset_targeted_dag.zip	 yolov8n_TrafficSigns.pt


In [7]:
# prompt: copy PGD_augmented_images.zip and fgsm_augmented_images.zip and Tdag_augmented_images.zip uap_augmented_images.zip to /content/

!cp /content/drive/MyDrive/yolo/PGD_augmented_images.zip /content/
!cp /content/drive/MyDrive/yolo/fgsm_augmented_images.zip /content/
!cp /content/drive/MyDrive/yolo/Tdag_augmented_images.zip /content/
!cp /content/drive/MyDrive/yolo/uap_augmented_images.zip /content/


In [8]:
# prompt: unzip Tdag_augmented_images

!unzip /content/Tdag_augmented_images.zip


Archive:  /content/Tdag_augmented_images.zip
   creating: content/Tdag_augmented_images/
   creating: content/Tdag_augmented_images/labels/
  inflating: content/Tdag_augmented_images/labels/adv_dag_000817_jpg.rf.68f00bacd64044c26863288fe30662fc.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_000876_jpg.rf.f1484438b786c9bc2472eb5256de0105.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_001628_JPG_jpg.rf.d9bd8fdce7633b12b74945d83f2ac9ae.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_road464_png.rf.4271b0c2de0fab3e46a1b9a33186641e.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_00001_00036_00016_png.rf.2e598c49c4d3a6bf8537f5b2fc81dacb.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_000962_jpg.rf.b13038a44582de579d9ebd346baca2dd.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_road474_png.rf.ad3e138e4e43508bccf7c4a88b3f0db6.txt  
  inflating: content/Tdag_augmented_images/labels/adv_dag_26e44f94

In [9]:
!mv /content/content/Tdag_augmented_images /content/Tdag_augmented_images

In [11]:
!rm -rf /content/content

In [12]:
# prompt: unzip PGD_augmented_images.zip

!unzip PGD_augmented_images.zip


Archive:  PGD_augmented_images.zip
   creating: content/PGD_augmented_images/
   creating: content/PGD_augmented_images/labels/
  inflating: content/PGD_augmented_images/labels/adv_pgd_00003_00027_00026_png.rf.240b0e4ec4b2a617a54b214a1ad6e622.txt  
  inflating: content/PGD_augmented_images/labels/adv_pgd_00008_00038_00019_png.rf.a453fa121b0c7df2bcf2a168ddd0fe66.txt  
  inflating: content/PGD_augmented_images/labels/adv_pgd_FisheyeCamera_1_00033_png.rf.6d65bd3913e93339bc15cbcdcec99ce3.txt  
  inflating: content/PGD_augmented_images/labels/adv_pgd_00002_00000_00026_png.rf.d46f9f6501359b9756c23e2262b3197e.txt  
  inflating: content/PGD_augmented_images/labels/adv_pgd_000847_jpg.rf.c628841b5736394b913c505851c45f05.txt  
  inflating: content/PGD_augmented_images/labels/adv_pgd_FisheyeCamera_1_00177_png.rf.4fd6ef4933c8ef258c42c8483dc6d9d7.txt  
  inflating: content/PGD_augmented_images/labels/adv_pgd_FisheyeCamera_1_00069_png.rf.899e0cd56a172c0588026638e986b1ae.txt  
  inflating: content/PGD

In [13]:
!mv /content/content/PGD_augmented_images /content/PGD_augmented_images
!rm -rf /content/content/

In [14]:
!unzip fgsm_augmented_images.zip
!mv /content/content/fgsm_augmented_images /content/fgsm_augmented_images
!rm -rf /content/content/

Archive:  fgsm_augmented_images.zip
   creating: content/fgsm_augmented_images/
   creating: content/fgsm_augmented_images/labels/
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_000565_jpg.rf.908fd7d48a31ba1b8bab45838b8b98c1.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_00002_00031_00027_png.rf.1487d6446c4d3d823ed1231bffd3f379.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_000480_jpg.rf.029085b0c7e0b472a6d3accbdb595884.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_road352_png.rf.9af0202482d2af127fed33305e693e71.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_road482_png.rf.ab577b8450c69f9d8cda37908dd216b9.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_00002_00015_00004_png.rf.bfac0c8d374b36dc75141baae164a658.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_000949_jpg.rf.c8b693b2ade3d9a716babda9890f18a2.txt  
  inflating: content/fgsm_augmented_images/labels/adv_fgsm_ro

In [15]:
!unzip uap_augmented_images.zip
!mv /content/content/uap_augmented_images /content/uap_augmented_images
!rm -rf /content/content/

Archive:  uap_augmented_images.zip
   creating: content/uap_augmented_images/
   creating: content/uap_augmented_images/labels/
  inflating: content/uap_augmented_images/labels/adv_uap_00000_00000_00011_png.rf.d90e4f357e6863b504552c29425e5a41.txt  
  inflating: content/uap_augmented_images/labels/adv_uap_00003_00000_00019_png.rf.9be039400ecf2ee302461849eb11c06e.txt  
  inflating: content/uap_augmented_images/labels/adv_uap_00001_00060_00000_png.rf.f147190985006ebe0a4886b529f9bd50.txt  
  inflating: content/uap_augmented_images/labels/adv_uap_000950_JPG_jpg.rf.ed045115e468d3a4f63990a2c7617745.txt  
  inflating: content/uap_augmented_images/labels/adv_uap_00000_00006_00029_png.rf.b4ad2ff118d9c1470180a74dbd7a662a.txt  
  inflating: content/uap_augmented_images/labels/adv_uap_road528_png.rf.318f9cf9f23f5e6b30faab08fd16fd0b.txt  
  inflating: content/uap_augmented_images/labels/adv_uap_FisheyeCamera_1_00362_png.rf.4f8f57c44b60eedbc040b81b67ab6238.txt  
  inflating: content/uap_augmented_ima

In [16]:
# prompt: merge content/PGD_augmented_images/images and content/fgsm_augmented_images/images and content/Tdag_augmented_images/images and content/uap_augmented_images/images images into /content/train/images

import shutil
from pathlib import Path

# Define source and destination directories
source_dirs = [
    "/content/PGD_augmented_images/images",
    "/content/fgsm_augmented_images/images",
    "/content/Tdag_augmented_images/images",
    "/content/uap_augmented_images/images",
]
destination_dir = "/content/train/images"

# Create the destination directory if it doesn't exist
Path(destination_dir).mkdir(parents=True, exist_ok=True)

# Iterate through source directories and copy images
for source_dir in source_dirs:
    for filename in Path(source_dir).glob("*"):
        if filename.is_file():
            shutil.copy2(filename, destination_dir) # copy2 preserves metadata


In [17]:
# prompt: how many files in /content/train/images

import os

image_dir = "/content/train/images"
num_files = len([f for f in os.listdir(image_dir) if os.path.isfile(os.path.join(image_dir, f))])
print(f"Number of files in {image_dir}: {num_files}")


Number of files in /content/train/images: 16072


In [18]:
# prompt: merge content/PGD_augmented_images/labels and content/fgsm_augmented_images/labels and content/Tdag_augmented_images/labels and content/uap_augmented_images/labels images into /content/train/labels

# Define source and destination directories for labels
source_dirs = [
    "/content/PGD_augmented_images/labels",
    "/content/fgsm_augmented_images/labels",
    "/content/Tdag_augmented_images/labels",
    "/content/uap_augmented_images/labels",
]
destination_dir = "/content/train/labels"

# Create the destination directory if it doesn't exist
Path(destination_dir).mkdir(parents=True, exist_ok=True)

# Iterate through source directories and copy labels
for source_dir in source_dirs:
    for filename in Path(source_dir).glob("*"):
        if filename.is_file():
            shutil.copy2(filename, destination_dir) # copy2 preserves metadata

#Verify number of labels
label_dir = "/content/train/labels"
num_files = len([f for f in os.listdir(label_dir) if os.path.isfile(os.path.join(label_dir, f))])
print(f"Number of files in {label_dir}: {num_files}")


Number of files in /content/train/labels: 16072


In [19]:
model = YOLO(model_path)


result = model.train(data='/content/data.yaml', epochs=10, batch=32)


Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: task=detect, mode=train, model=/content/drive/MyDrive/yolo/yolov8n_TrafficSigns.pt, data=/content/data.yaml, epochs=10, time=None, patience=100, batch=32, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=T

100%|██████████| 755k/755k [00:00<00:00, 22.6MB/s]



                   from  n    params  module                                       arguments                     
  0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
  1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
  2                  -1  1      7360  ultralytics.nn.modules.block.C2f             [32, 32, 1, True]             
  3                  -1  1     18560  ultralytics.nn.modules.conv.Conv             [32, 64, 3, 2]                
  4                  -1  2     49664  ultralytics.nn.modules.block.C2f             [64, 64, 2, True]             
  5                  -1  1     73984  ultralytics.nn.modules.conv.Conv             [64, 128, 3, 2]               
  6                  -1  2    197632  ultralytics.nn.modules.block.C2f             [128, 128, 2, True]           
  7                  -1  1    295424  ultralytics.nn.modules.conv.Conv             [128

100%|██████████| 5.35M/5.35M [00:00<00:00, 95.1MB/s]


AMP: checks passed ✅


...

      10/10      5.11G     0.5327     0.3773     0.9551         12        640: 100%|██████████| 503/503 [05:21<00:00,  1.56it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 13/13 [00:06<00:00,  1.87it/s]

                   all        801        944       0.93      0.924      0.957      0.824



10 epochs completed in 0.926 hours.
Optimizer stripped from runs/detect/train/weights/last.pt, 6.2MB
Optimizer stripped from runs/detect/train/weights/best.pt, 6.2MB

Validating runs/detect/train/weights/best.pt...
Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
Model summary (fused): 72 layers, 3,008,573 parameters, 0 gradients, 8.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 13/13 [00:12<00:00,  1.05it/s]


                   all        801        944       0.93      0.924      0.957      0.823
           Green Light         87        122      0.857      0.739      0.845      0.515
             Red Light         74        108      0.829       0.75      0.821      0.498
       Speed Limit 100         52         52      0.868      0.981      0.989      0.883
       Speed Limit 110         17         17      0.763      0.945      0.937      0.846
       Speed Limit 120         60         60          1      0.946      0.995      0.913
        Speed Limit 20         56         56      0.988      0.982      0.987      0.883
        Speed Limit 30         71         74      0.964      0.959      0.989      0.908
        Speed Limit 40         53         55      0.922      0.982      0.992      0.883
        Speed Limit 50         68         71      0.961      0.944      0.966      0.858
        Speed Limit 60         76         76      0.959      0.915       0.96      0.872
        Speed Limit 7

In [20]:
# Save the trained model to Google Drive
model_save_path = '/content/drive/MyDrive/yolo/yolov8n_TrafficSigns_defence2.pt'
model.export(format='onnx', imgsz=640, dynamic=True)
model.save(model_save_path)
print(f"Model saved to: {model_save_path}")

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CPU (Intel Xeon 2.00GHz)
Model summary (fused): 72 layers, 3,008,573 parameters, 0 gradients, 8.1 GFLOPs

PyTorch: starting from 'runs/detect/train/weights/best.pt' with input shape (1, 3, 640, 640) BCHW and output shape(s) (1, 19, 8400) (6.0 MB)
requirements: Ultralytics requirements ['onnx>=1.12.0', 'onnxslim', 'onnxruntime-gpu'] not found, attempting AutoUpdate...
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.0/16.0 MB 294.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 144.5/144.5 kB 207.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 280.8/280.8 MB 244.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 183.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 248.2 MB/s eta 0:00:00

requirements: AutoUpdate success ✅ 17.0s, installed 3 packages: ['onnx>=1.12.0', 'onnxslim', 'onnxruntime-gpu']
requirements: ⚠️ Restart runtime or rerun command for update

In [21]:
# Evaluate on the test set
results = model.val(
    data="/content/data.yaml",
    split="test",  # Explicitly specify the test split
    batch=32,      # Adjust based on GPU memory
    imgsz=640,      # Match training image size
    conf= 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
Model summary (fused): 72 layers, 3,008,573 parameters, 0 gradients, 8.1 GFLOPs


val: Scanning /content/test/labels... 638 images, 1 backgrounds, 0 corrupt: 100%|██████████| 638/638 [00:00<00:00, 645.91it/s]

val: New cache created: /content/test/labels.cache



                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:08<00:00,  2.26it/s]


                   all        638        770      0.907      0.875      0.939      0.823
           Green Light         77        110      0.943      0.751      0.884      0.598
             Red Light         71         94      0.857      0.723      0.822      0.543
        Speed Limit 10          2          3      0.458      0.667       0.83      0.692
       Speed Limit 100         45         46      0.914      0.913       0.96      0.865
       Speed Limit 110         21         21      0.948      0.867      0.955      0.855
       Speed Limit 120         40         44      0.912      0.932      0.967      0.888
        Speed Limit 20         46         46      0.959      0.957      0.975      0.898
        Speed Limit 30         60         60      0.857      0.867      0.929       0.88
        Speed Limit 40         51         53          1      0.969       0.99      0.876
        Speed Limit 50         47         50      0.935       0.86      0.943      0.866
        Speed Limit 6

In [23]:
!cp /content/drive/MyDrive/yolo/adversarial_data_set_pgd_1.zip /content/


'\n!cp /content/drive/MyDrive/yolo/adversarial_data_set_pgd_02.zip\n!cp /content/drive/MyDrive/yolo/adversarial_data_set_fgsm.zip\n!cp /content/drive/MyDrive/yolo/adversarial_data_set_dis_dag.zip\n!cp /content/drive/MyDrive/yolo/adversarial_data_set_targeted_dag.zip\n!cp /content/drive/MyDrive/yolo/adversarial_data_set_fool_detectors.zip\n'

In [30]:

!unzip adversarial_data_set_pgd_1.zip -d /content/


Archive:  adversarial_data_set_pgd_1.zip
replace /content/content/adversarial_dataset/labels.cache? [y]es, [n]o, [A]ll, [N]one, [r]ename: A
  inflating: /content/content/adversarial_dataset/labels.cache  
  inflating: /content/content/adversarial_dataset/labels/00004_00060_00021_png.rf.a81a5ba2fb654d944063ddd496a46662.txt  
  inflating: /content/content/adversarial_dataset/labels/road446_png.rf.c209c8b5929313d1258667af1a6a37ae.txt  
  inflating: /content/content/adversarial_dataset/labels/00001_00028_00017_png.rf.98d01270a314b8cc77f6ad92f979b47f.txt  
  inflating: /content/content/adversarial_dataset/labels/001261_jpg.rf.7aab90697a4784411cbc2785e626e004.txt  
  inflating: /content/content/adversarial_dataset/labels/road59_png.rf.40b97d5dddbee9679979779c88bb7348.txt  
  inflating: /content/content/adversarial_dataset/labels/000811_jpg.rf.f5bb7753902ae5b5fd8f5e7f601da271.txt  
  inflating: /content/content/adversarial_dataset/labels/road692_png.rf.ab199ab022b948479bfba7b3c8fd66dd.txt  
 

In [ ]:
# Evaluate pgd with 0.1 epsilon
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels.cache... 636 images, 1 backgrounds, 0 corrupt: 100%|██████████| 636/636 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:16<00:00,  1.22it/s]


                   all        636        768      0.858      0.884      0.915      0.792
           Green Light         77        110      0.843      0.782       0.86      0.539
             Red Light         71         94      0.756      0.691      0.779      0.503
        Speed Limit 10          2          3        0.6          1      0.863      0.751
       Speed Limit 100         45         46      0.824      0.913      0.938      0.837
       Speed Limit 110         21         21        0.9      0.857      0.892      0.794
       Speed Limit 120         40         44      0.833      0.909      0.923      0.839
        Speed Limit 20         46         46      0.898      0.957      0.976      0.884
        Speed Limit 30         60         60      0.823       0.85      0.888      0.829
        Speed Limit 40         51         53      0.881      0.981      0.982      0.861
        Speed Limit 50         46         49      0.863      0.898      0.932      0.853
        Speed Limit 6

In [58]:
!cp /content/drive/MyDrive/yolo/adversarial_data_set_fgsm.zip /content/

!unzip adversarial_data_set_fgsm.zip -d /content/


Archive:  adversarial_data_set_fgsm.zip
   creating: /content/content/adversarial_dataset/
   creating: /content/content/adversarial_dataset/labels/
  inflating: /content/content/adversarial_dataset/labels/road466_png.rf.e1995d1db602b4fe4f26c9a2f882bf06.txt  
  inflating: /content/content/adversarial_dataset/labels/road654_png.rf.46b39454d20cf1f488267148cc1ee23c.txt  
  inflating: /content/content/adversarial_dataset/labels/road314_png.rf.b9b5f3356645589e1d35652eaf64b5bf.txt  
  inflating: /content/content/adversarial_dataset/labels/00005_00016_00001_png.rf.8ed5c07e98a19127d55583cbd0ebabfb.txt  
  inflating: /content/content/adversarial_dataset/labels/00002_00032_00021_png.rf.da1c231b696e926dff55375e5718a461.txt  
  inflating: /content/content/adversarial_dataset/labels/road108_png.rf.3ccb5b5dbd4fe2ff044ce6f2aed3cf40.txt  
  inflating: /content/content/adversarial_dataset/labels/643854b9-b9d9-4b74-99fb-830fde4a0b74_jpg.rf.70299bd9ade4fba6166556c81ee6a4c0.txt  
  inflating: /content/con

In [59]:
!mv /content/content/adversarial_dataset/ /content/adversarial_dataset
!rm -rf /content/content/

In [60]:
# Evaluate fgsm
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels.cache... 638 images, 1 backgrounds, 0 corrupt: 100%|██████████| 638/638 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:14<00:00,  1.35it/s]


                   all        638        770      0.879      0.751      0.864      0.741
           Green Light         77        110      0.915      0.489      0.748      0.468
             Red Light         71         94      0.775      0.447      0.637      0.404
        Speed Limit 10          2          3      0.741          1      0.995      0.816
       Speed Limit 100         45         46      0.842      0.696      0.845      0.755
       Speed Limit 110         21         21      0.816      0.634      0.824      0.739
       Speed Limit 120         40         44      0.868      0.795       0.88      0.758
        Speed Limit 20         46         46      0.946      0.935      0.969      0.853
        Speed Limit 30         60         60      0.874      0.809      0.866      0.798
        Speed Limit 40         51         53      0.826      0.807      0.882      0.769
        Speed Limit 50         47         50       0.88      0.736      0.864       0.77
        Speed Limit 6

In [64]:
!rm -rf /content/adversarial_dataset/
!cp /content/drive/MyDrive/yolo/adversarial_dataset_targeted_dag.zip /content/
!unzip adversarial_dataset_targeted_dag.zip -d /content/
!mv /content/content/adversarial_dataset/ /content/adversarial_dataset
!rm -rf /content/content/

Archive:  adversarial_dataset_targeted_dag.zip
   creating: /content/adversarial_dataset_targeted_dag/
   creating: /content/adversarial_dataset_targeted_dag/content/
   creating: /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/
  inflating: /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/labels.cache  
   creating: /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/images/
  inflating: /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/images/road321_png.rf.273e027200cfc85d8f8084d63ca95d07.png  
  inflating: /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/images/road708_png.rf.4770835b7ec7f0e5c66a8a9ec37d5ee2.png  
  inflating: /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/images/000626_jpg.rf.b953e9072596ff4b4b28334c314e2d56.png  
  inflating: /content/adversarial_dataset_targeted_dag/content/adversarial_

In [70]:
!mv /content/adversarial_dataset_targeted_dag/content/adversarial_dataset_targeted/ /content/adversarial_dataset/

In [71]:
!rm -rf /content/adversarial_dataset_targeted_dag

In [72]:
# Evaluate targeted dag
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels... 638 images, 1 backgrounds, 0 corrupt: 100%|██████████| 638/638 [00:00<00:00, 841.66it/s]

val: New cache created: /content/adversarial_dataset/labels.cache



                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:15<00:00,  1.30it/s]


                   all        638        770      0.881      0.847      0.915      0.802
           Green Light         77        110       0.93      0.726      0.861      0.587
             Red Light         71         94      0.861      0.661      0.806      0.525
        Speed Limit 10          2          3      0.443      0.667      0.732      0.626
       Speed Limit 100         45         46       0.87      0.891      0.945      0.853
       Speed Limit 110         21         21      0.899       0.81      0.916      0.825
       Speed Limit 120         40         44      0.906      0.878      0.927      0.851
        Speed Limit 20         46         46      0.905      0.957      0.975      0.887
        Speed Limit 30         60         60      0.851      0.857      0.925      0.872
        Speed Limit 40         51         53      0.967      0.925      0.975      0.852
        Speed Limit 50         47         50      0.846       0.88      0.923      0.849
        Speed Limit 6

In [78]:
!rm -rf /content/adversarial_dataset/
!cp /content/drive/MyDrive/yolo/adversarial_data_set_UAP.zip /content/
!unzip adversarial_data_set_UAP.zip -d /content/
!mv /content/content/adversarial_dataset/ /content/adversarial_dataset

^C
Archive:  adversarial_data_set_UAP.zip
  End-of-central-directory signature not found.  Either this file is not
  a zipfile, or it constitutes one disk of a multi-part archive.  In the
  latter case the central directory and zipfile comment will be found on
  the last disk(s) of this archive.
unzip:  cannot find zipfile directory in one of adversarial_data_set_UAP.zip or
        adversarial_data_set_UAP.zip.zip, and cannot find adversarial_data_set_UAP.zip.ZIP, period.
mv: cannot stat '/content/content/adversarial_dataset/': No such file or directory


In [74]:
# Evaluate uap
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels.cache... 638 images, 1 backgrounds, 0 corrupt: 100%|██████████| 638/638 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:16<00:00,  1.22it/s]


                   all        638        770      0.932      0.831      0.917      0.802
           Green Light         77        110      0.923      0.652      0.827      0.562
             Red Light         71         94      0.888      0.588      0.779      0.512
        Speed Limit 10          2          3      0.682      0.667      0.806      0.669
       Speed Limit 100         45         46      0.954      0.909      0.949      0.858
       Speed Limit 110         21         21      0.943      0.789       0.91      0.837
       Speed Limit 120         40         44      0.932      0.937      0.965       0.87
        Speed Limit 20         46         46       0.96      0.935       0.97       0.89
        Speed Limit 30         60         60      0.928       0.85      0.913      0.862
        Speed Limit 40         51         53          1      0.943      0.979      0.861
        Speed Limit 50         47         50      0.931      0.814      0.921      0.847
        Speed Limit 6

In [80]:
!rm -rf /content/adversarial_dataset/

In [93]:
!cp /content/drive/MyDrive/yolo/adversarial_data_set_fool_detectors.zip /content/
!unzip adversarial_data_set_fool_detectors.zip -d /content/
!mv /content/content/adversarial_dataset/ /content/adversarial_dataset

^C
Archive:  adversarial_data_set_fool_detectors.zip
  End-of-central-directory signature not found.  Either this file is not
  a zipfile, or it constitutes one disk of a multi-part archive.  In the
  latter case the central directory and zipfile comment will be found on
  the last disk(s) of this archive.
unzip:  cannot find zipfile directory in one of adversarial_data_set_fool_detectors.zip or
        adversarial_data_set_fool_detectors.zip.zip, and cannot find adversarial_data_set_fool_detectors.zip.ZIP, period.
mv: cannot stat '/content/content/adversarial_dataset/': No such file or directory


In [88]:
# Evaluate fool detectors (didn't do adversarial training with it )
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels... 638 images, 1 backgrounds, 0 corrupt: 100%|██████████| 638/638 [00:00<00:00, 903.26it/s]

val: New cache created: /content/adversarial_dataset/labels.cache



                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:16<00:00,  1.24it/s]


                   all        638        770      0.918      0.786      0.897      0.786
           Green Light         77        110      0.985       0.58      0.841       0.58
             Red Light         71         94      0.938      0.482      0.779      0.517
        Speed Limit 10          2          3       0.65      0.667      0.732      0.626
       Speed Limit 100         45         46      0.932      0.826      0.919      0.816
       Speed Limit 110         21         21      0.884      0.728      0.903       0.81
       Speed Limit 120         40         44      0.931      0.841      0.924      0.844
        Speed Limit 20         46         46      0.933      0.935      0.955      0.879
        Speed Limit 30         60         60      0.846      0.817      0.875      0.824
        Speed Limit 40         51         53       0.99      0.906       0.97      0.848
        Speed Limit 50         47         50      0.835      0.809      0.895      0.814
        Speed Limit 6

In [92]:
!rm -rf /content/adversarial_dataset/

In [94]:
!cp /content/drive/MyDrive/yolo/adversarial_data_set_dis_dag.zip /content/
!unzip adversarial_data_set_dis_dag.zip -d /content/

Archive:  adversarial_data_set_dis_dag.zip
   creating: /content/adversarial_data_set_dis_dag/
   creating: /content/adversarial_data_set_dis_dag/content/
   creating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/
  inflating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/labels.cache  
   creating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/images/
  inflating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/images/000359_jpg.rf.786658c4016fb105872988bc5cc4a3b3.png  
  inflating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/images/000099_jpg.rf.4f6c946e5e6bada45a6ed26cde81e0c7.png  
  inflating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/images/00014_00008_00013_png.rf.305dac45aa2ed53fd76943f24ae668c2.png  
  inflating: /content/adversarial_data_set_dis_dag/content/adversarial_dataset/images/00014_00004_00010_png.rf.66187010c62b6f44f2dec0d41a63b804.png  
  infl

In [101]:
!mv adversarial_data_set_dis_dag/content/adversarial_dataset/ /content/adversarial_dataset/

In [116]:
# Evaluate dis dag (didn't do adversarial training with it )
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels... 113 images, 0 backgrounds, 0 corrupt: 100%|██████████| 113/113 [00:00<00:00, 949.10it/s]

val: New cache created: /content/adversarial_dataset/labels.cache



                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 4/4 [00:04<00:00,  1.15s/it]


                   all        113        139      0.906      0.897      0.937      0.833
           Green Light         14         23          1      0.665       0.87      0.587
             Red Light          9         12      0.682      0.716      0.752      0.496
       Speed Limit 100          5          6      0.927          1      0.995      0.885
       Speed Limit 110          3          3      0.776          1      0.995      0.896
       Speed Limit 120          4          8      0.811      0.875      0.924      0.821
        Speed Limit 20         11         11      0.917          1      0.988      0.907
        Speed Limit 30          8          8      0.833      0.625      0.781      0.767
        Speed Limit 40          5          5          1          1      0.995      0.918
        Speed Limit 50          8          8      0.887       0.98      0.982      0.901
        Speed Limit 60          7          7      0.902          1      0.995      0.914
        Speed Limit 7

In [119]:
!rm -rf /content/adversarial_dataset/

In [120]:
!cp /content/drive/MyDrive/yolo/adversarial_data_set_pgd_02.zip /content/
!unzip adversarial_data_set_pgd_02.zip -d /content/
!mv /content/content/adversarial_dataset/ /content/adversarial_dataset

Archive:  adversarial_data_set_pgd_02.zip
   creating: /content/content/adversarial_dataset/
  inflating: /content/content/adversarial_dataset/labels.cache  
   creating: /content/content/adversarial_dataset/labels/
  inflating: /content/content/adversarial_dataset/labels/00004_00060_00021_png.rf.a81a5ba2fb654d944063ddd496a46662.txt  
  inflating: /content/content/adversarial_dataset/labels/road446_png.rf.c209c8b5929313d1258667af1a6a37ae.txt  
  inflating: /content/content/adversarial_dataset/labels/00001_00028_00017_png.rf.98d01270a314b8cc77f6ad92f979b47f.txt  
  inflating: /content/content/adversarial_dataset/labels/001261_jpg.rf.7aab90697a4784411cbc2785e626e004.txt  
  inflating: /content/content/adversarial_dataset/labels/road59_png.rf.40b97d5dddbee9679979779c88bb7348.txt  
  inflating: /content/content/adversarial_dataset/labels/000811_jpg.rf.f5bb7753902ae5b5fd8f5e7f601da271.txt  
  inflating: /content/content/adversarial_dataset/labels/road692_png.rf.ab199ab022b948479bfba7b3c8fd6

In [121]:
# Evaluate PGD 0.02 (didn't do adversarial training with it )
results = model.val(
    data="/content/adv.yaml",
    split="test",  # Not actually used but required by API
    imgsz=640,
    batch=32,
    conf = 0.25
)

Ultralytics 8.3.107 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)


val: Scanning /content/adversarial_dataset/labels.cache... 629 images, 1 backgrounds, 0 corrupt: 100%|██████████| 629/629 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 20/20 [00:14<00:00,  1.37it/s]


                   all        629        760      0.931      0.848      0.938       0.82
           Green Light         74        107      0.952      0.735      0.886      0.598
             Red Light         70         93      0.911       0.66      0.832      0.543
        Speed Limit 10          2          3      0.659      0.667       0.83      0.691
       Speed Limit 100         44         45      0.933      0.933      0.968      0.874
       Speed Limit 110         19         19          1      0.824      0.966      0.871
       Speed Limit 120         39         43      0.908      0.913      0.964       0.88
        Speed Limit 20         46         46      0.967      0.957      0.976      0.897
        Speed Limit 30         60         60      0.862       0.85       0.92      0.864
        Speed Limit 40         51         53          1      0.933      0.979       0.87
        Speed Limit 50         47         50      0.909       0.86      0.932      0.854
        Speed Limit 6

## mAP@0.5 results after multi-attack adversarial training with 5,500 adversarial images (2,000 PGD, 1,500 FGSM, 500 Targeted DAG, 1,500 UAP) on top of your 10,590 clean images.
| Attack Technique        | Clean mAP@0.5 | Adv mAP@0.5 (Pre-adversarial training) | Adv mAP@0.5 (Post-adversarial Training) | Drop (Pre) | Drop (Post) | Notes |
|-------------------------|---------------|----------------------------|-----------------------------|------------|-------------|-------|
| Clean                   | 0.927         | -                          | 0.939                       | -          | -           | Slight clean mAP improvement (+0.012) |
| FGSM                    | 0.927         | 0.312                      | 0.864                       | -0.615     | -0.075      | Significant gain (+0.552), but still weakest |
| PGD (ε=0.1, α=0.025)    | 0.927         | 0.215                      | 0.915                       | -0.712     | -0.024      | Strong improvement (+0.700), very robust |
| Targeted DAG            | 0.927         | 0.0947                     | 0.915                       | -0.8323    | -0.024      | Huge gain (+0.8203), matches PGD robustness |
| UAP                     | 0.927         | 0.443                      | 0.917                       | -0.484     | -0.022      | Large gain (+0.474), near-clean performance |
| Fool Detectors          | 0.927         | 0.155                      | 0.897                       | -0.772     | -0.042      | Good gain (+0.742), but not trained on |
| Disappearance DAG       | 0.927         | 0.547                      | 0.937                       | -0.388     | -0.002      | Excellent (+0.390), near-clean, not trained on |
| PGD (ε=0.02, α=0.005)   | 0.927         | 0.617                      | 0.938                       | -0.310     | -0.001      | Near-perfect (+0.321), not trained on |